**This notebook is the executable version of lab note 3.
It answers the following questions:**

Finally, we answer 4 items:

    1. Are successful creators more connected to high-outdegree users than do unsuccessful creators?
    2. Are mavens more connected to successful creators than to unsuccessful creators?
    3. Do successful creators send more non-follow actions towards mavens than to zombies?
    4. Do successful creators send more non-follow actions towards mavens than to stars?

    

In [1]:
#Run parameters
#used to control every run. Can be user to perfom sensitivity checks
path_dir = r"/Users/../Volumes/Raw/"

low_success = 0.5 #below the median: unsuccessful
high_success = 0.9 #top 10% creators with more followers are deemed successful

low_user_outdegree = 0.25 
high_user_outdegree = 0.75
low_user_activity = 0.25 
high_user_activity = 0.75 

activity_filter = 0
days_delta = 7

In [2]:
import sys  
import pickle
sys.path.insert(0, '/Users/caiorego/Desktop/BDS/RA/Seeding-Bandits/')
import numpy as np
import src.utils
from collections import Counter
from src.utils import import_dta, import_tracks_dta,\
gen_active_relations, get_fan_interactions_per_week, calculate_avg_monthly_valence,\
gen_active_relations_prob, get_fan_interactions_per_week_prob, stripplot_prob,\
reaction_probability, follower_list, filter_quantile, sample_creators_music,\
gen_outbound_creators
import numpy as np
import datetime
import pandas as pd
from tqdm import tqdm
import dask.dataframe as dd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy
import os
from statsmodels.stats.proportion import proportions_ztest
from datetime import datetime, timedelta


In [19]:
def process_date(date):
    '''convert date format like '2013-w09' to '2013-03-04', i.e. the first day of that week'''
    year = date[0:4]
    week = date[6:]
    day = "1"
    date = "{}-{}-1".format(year, week)
    dt = datetime.strptime(date, "%Y-%W-%w")
    return dt

# Data Imports

We start by importing the raw data.  `follows_sent`, `comments_sent`, `shares_sent`, `likes_sent` and `messages_sent` contains data pn the promotional activities that the 35k users tracked in the dataset directed to other users. It includes the `user_id`, the `fan_id` and the `date_sent` which identifies the date when the prom. activity was sent. `users_info_1st` shows the type of user (creator or non-creator, which is identified by a blank) and the date the user entered the platform, for every user that sent or received prom. activities from any of the 35k users tracked in this dataset, while `users_info` contains the same information, but pertaining to the 35k users themselves.

`follows_received` contains information on the follows received by the 35k users and will be used to generate the successful/unsuccessful groups of content creators.

In [4]:
#affiliations :follows
#favoritings :likes

#used in filtering:
path_dir = r"/Users/../Volumes/Raw/"
tracks = import_tracks_dta(path_dir, "12sample_tracks.dta");

#these are the actions sent to 
follows_sent = import_dta(path_dir, "12sample_affiliations_sent.dta");
comments_sent = import_dta(path_dir, "12sample_comments_made.dta");
shares_sent = import_dta(path_dir, "12sample_reposts_made.dta");
likes_sent = import_dta(path_dir, "12sample_favoritings_made.dta");
messages_sent = import_dta(path_dir, "12sample_messages_sent.dta");

#Used to track information on the 1st degree connections
user_info_1st = import_dta(path_dir, "12sample_1st_deg_user_infos.dta");
user_info_1st.columns = ['user_id', 'type', 'entered_platform'];
user_info = import_dta(path_dir, "12sample_user_infos.dta");

#Used to compute creator's success measure
follows_received = import_dta(path_dir, "12sample_affiliations_received.dta");

%%%%%%%%%% 12sample_tracks.dta %%%%%%%%%%
(56262, 7)
%%%%%%%%%% 12sample_affiliations_sent.dta %%%%%%%%%%
(800913, 3)
%%%%%%%%%% 12sample_comments_made.dta %%%%%%%%%%
(29258, 4)
%%%%%%%%%% 12sample_reposts_made.dta %%%%%%%%%%
(179329, 4)
%%%%%%%%%% 12sample_favoritings_made.dta %%%%%%%%%%
(527701, 4)
%%%%%%%%%% 12sample_messages_sent.dta %%%%%%%%%%
(11091, 3)
%%%%%%%%%% 12sample_1st_deg_user_infos.dta %%%%%%%%%%
(670746, 3)
%%%%%%%%%% 12sample_user_infos.dta %%%%%%%%%%
(35000, 3)
%%%%%%%%%% 12sample_affiliations_received.dta %%%%%%%%%%
(432503, 3)


Indegree and outdegree information.

The function below import the outdegree dataset. Because the raw version of those dataset are too large to be processed in memory, we preprocessed them in a separate script.

In [5]:
# Aggregates preprocessed outdegree of 1st degree users
def import_outdegree(path='/Users/caiorego/Desktop/BDS/RA/Seeding-Bandits/'):
    d = {}
    for i in range(6):
       d[str(i)] = pd.read_pickle(os.path.join(path,'{}.pkl'.format(i))) 
       d[str(i)]['created_at'] =  pd.to_datetime(d[str(i)]['created_at'])
       d[str(i)]['created_at'] = pd.to_datetime(d[str(i)]['created_at']).dt.floor('d')
       d[str(i)] = d[str(i)].groupby(['sender_id', 'created_at'], as_index = False).size() 
    
    data_outdegree = pd.concat([d['0'], d['1'], d['2'], d['3'], d['4'], d['5']])
    #data_outdegree.set_index('created_at', inplace = True)
    return data_outdegree

In [6]:
data_outdegree = import_outdegree()

In [7]:
#data_outdegree = data_outdegree.groupby(['sender_id','created_at'], as_index = False).size()

# Preprocessing

## Creator ids, successful and unsucessful creators

Next, we define three lists of ids: one with the ids from the content creators, according to the `users_info` table, one with the ids of successful creators and the last one with the ids of the unsuccessful ones.

Let's start with a list of the id of creators. We also create a dataset with containing information on creators only.

In [8]:
mask = (tracks.track_available == 1) & (tracks.public == 't')
creator_ids = tracks[mask].user_id.unique()

creators = tracks[(tracks.track_available == 1) & (tracks.public == 't')]

#mask = user_info.type == 'creator'
#creator_ids = user_info[mask].user_id.unique()

#creators = user_info[user_info.type == 'creator']

## Putting together a dataset with the promotional activities made by content creators.

The function `gen_actions_sent_df` creates a dataframe with all the promotional activities that content creators sent to users.

In [9]:
def gen_actions_sent_df(follows_sent, shares_sent, likes_sent, comments_sent, messages_sent, creator_ids = creator_ids):
    '''
    Creates dataframe containing the actions that content creators send to users.
        Attributes:
                    follows_sent:  dataframe with the follows sent by the 35k users.
                    shares_sent:   dataframe with the shares sent by the 35k users.
                    likes_sent:    dataframe with the likes sent by the 35k users.
                    comments_sent: dataframe with the comments sent by the 35k users.
                    messages_sent: dataframe with the messages sent by the 35k users.
                    creator_ids:   list with content creator ids. If not none, is used to
                                   filter out activities from non creators.
    '''
    
    follows_sent['outbound_activity'] = 'follow'
    follows_sent.columns = ['user_id', 'fan_id', 'date_sent', 'outbound_activity']

    if 'song_id' in shares_sent.columns:
        shares_sent.drop(columns=["song_id"])
    shares_sent = shares_sent[['reposter_id', "owner_id", 'created_at']]
    shares_sent['outbound_activity'] = 'share'
    shares_sent.columns = ['user_id', 'fan_id', 'date_sent', 'outbound_activity']

    if 'track_id' in likes_sent.columns:
        likes_sent.drop(columns=["track_id"], inplace=True)
    likes_sent['outbound_activity'] = 'like'
    likes_sent.columns = ['user_id', 'fan_id', 'date_sent', 'outbound_activity']

    if 'track_id' in comments_sent.columns:
        comments_sent.drop(columns=["track_id"], inplace=True)
    comments_sent['outbound_activity'] = 'comment'
    comments_sent.columns = ['user_id', 'fan_id', 'date_sent', 'outbound_activity']

    messages_sent["outbound_activity"] = 'message'
    messages_sent.columns = ['user_id', 'fan_id', 'date_sent', 'outbound_activity']
    df = pd.concat([follows_sent, shares_sent, likes_sent, comments_sent, messages_sent])


    if type(creator_ids) == numpy.ndarray:
        df = df[df['user_id'].isin(creator_ids)]
        
    df['week_yr'] = df.date_sent.dt.strftime('%Y-w%U')
    df = df.loc[df['user_id'] != df['fan_id'],:]

    return df

In [10]:
actions_sent = gen_actions_sent_df(follows_sent, shares_sent, likes_sent, comments_sent,
                                     messages_sent, creator_ids = None)
actions_sent = actions_sent.loc[actions_sent.user_id.isin(creators.user_id.unique())]

In [11]:
active_users_ids = actions_sent.groupby('user_id', as_index = False).size()
mask = active_users_ids['size']>= activity_filter
active_users_ids = active_users_ids[mask].user_id.unique()

In [12]:
def successful_creators_followers(follows_received, base_date = datetime(2016, 5, 30, 0, 0), perc1 = None, perc2 = None, subset_creators = None):
    '''Classifies content creators in successful or unsuccessfull
        Arguments:
                    follows_received: dataframe containing the follows received by content creators
                    base date:        date, in datetime.datetime(YYYY, M, DD, H, M) format, in which the number 
                                      of followers per creator is calculated.
                    perc1:            the threshold used to classify unsuccessful content creators. Creator having 
                                      total followers below the number dictated by this threshold, at the base date,
                                      are classified as unsuccessful 
                    perc2:            the threshold used to classify successful content creators. Creator having 
                                      total followers above the number dictated by this threshold, at the base date,
                                      are classified as successful
                    subset_creators:  a pd.DataFrame containing the creators. If is it available, it will be used to 
                                      filter out non creators and to make sure creators with 0 followers are part of
                                      the resulting dataset.
        
    '''
    print(base_date)

    if 'inbound_activity' not in follows_received.columns:
        follows_received.columns = ['fan_id', 'user_id', 'date_sent']

    mask = (follows_received['date_sent'] < base_date)

    df = follows_received[mask].groupby('user_id', as_index=False).agg({'fan_id': pd.Series.nunique})
    df.columns = ['user_id', 'followers']

    
    if type(subset_creators) == pd.DataFrame:
        print('subsetting...')
        df.set_index('user_id', inplace = True)
        df = df.reindex(subset_creators.user_id.unique())
        df.fillna(0, inplace = True)
        df.reset_index(inplace = True)
        df.columns = ['user_id', 'followers']
        
    mask = df.user_id.isin(active_users_ids)
    df = df[mask]

    low = np.quantile(df.followers, perc1)
    high = np.quantile(df.followers, perc2)

    print("High influencer boundary: {}".format(high))
    print("Low influencer boundary: {}".format(low))

    mask = (df["followers"] <= low) | (df["followers"] >= high)
    
    unsuccessful_creator_ids = df.loc[df["followers"] <= low].user_id.unique()
    successful_creator_ids = df.loc[df["followers"] >= high].user_id.unique()

    return unsuccessful_creator_ids, successful_creator_ids


In [13]:
unsuccessful_ids, successful_ids = successful_creators_followers(follows_received, 
                                                        perc1 = low_success, perc2 = high_success, subset_creators = creators)


2016-05-30 00:00:00
subsetting...
High influencer boundary: 81.0
Low influencer boundary: 13.0


In [ ]:
print(len(unsuccessful_ids))
print(len(successful_ids))

In [ ]:
creators.user_id.nunique()

## Filter only actions that were sent to non-fans

We merge the `actions_sent` dataset with a table containing the date each fan started following the creator.

In [14]:
follows_received.columns = ['fan_id', 'user_id', 'date_sent']
followers = follows_received[["fan_id", "user_id", "date_sent"]]
followers.columns = ["fan_id", "user_id", "follower_since"]

actions_sent = actions_sent.merge(followers, right_on = ['user_id', 'fan_id'],
                                      left_on = ['user_id', 'fan_id'], how = 'left')

Since we are interested in acquisition campaings, we need to produce a dataset that exclude actions targetting fans.
We do that using filters based on the date of the action and the date that the user became a fan of the content creator. The resulting dataframe is named `actions_sent_non_fans`.

We then filter only actions that happened before the user follows the content creator.

In [20]:
mask = (actions_sent.date_sent < actions_sent.follower_since) | (actions_sent.follower_since.isnull())
actions_sent_non_fans =  actions_sent[mask]
actions_sent_non_fans['week_yr_date'] = actions_sent_non_fans.week_yr.apply(lambda x: process_date(x))

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/3855957735.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  actions_sent_non_fans['week_yr_date'] = actions_sent_non_fans.week_yr.apply(lambda x: process_date(x))


## Outdegree level

Originally, we only have outdegree information on users that follow at least one user. The function below inputs an outdegree of 0 to users that are following anyone.

In [21]:
#CHANGE DOCUMENTATION
def outdegree_level(data, date, user_info = user_info_1st):
    
    '''
    This function returns the membership table at date equals `date`. Every user that interacted with the 35k tracked 
    users and entered the platform before `date` is present in the table, even if it has indegree 0.
    arguments:
              data:           the indegree dataset.
              user_info:      the dataset containing all the users that interacted with the 35k users tracked.
    '''
    
    data = data[data.created_at.dt.floor('d')<=date]
    data = data.groupby('sender_id').agg({'size':'sum'}).compute()
    
    #merge with user info to obtain users that are not followed by anyone at the current date
    data = user_info_1st.merge(data, left_on = 'user_id', right_on = 'sender_id', how= 'outer')
    data.loc[data['size'].isnull(), 'size'] = 0
    data = data[['user_id', 'size', 'entered_platform']].set_index('user_id')
    
    #filter out users that didnt exist in the current date
    mask = data['entered_platform'].dt.floor('d') <= date
    data = data.loc[mask]
    
    mask = (data['size']>0)
    data.loc[~mask, 'size'] = 0 
    
    return data

In [22]:
#dask is a python api with objects optimized for big data (user directed acyclic graphs). 
dask_outdegree = dd.from_pandas(data_outdegree, npartitions = 3)

In [23]:
last_day =  max(actions_sent.date_sent.dt.floor('d').unique())
user_outdegree = outdegree_level(dask_outdegree, last_day, user_info = user_info_1st)

Now we classify the creator in successful and unsuccessful, according to the threshold defined in the beggining of this notebook.

In [24]:
def user_outdegree_level(oudegree_data, perc1 = None, perc2 = None):
    '''Classifies content creators in successful or unsuccessfull
        Arguments:
                    oudegree_data:    dataframe containing the fans followers at 
                    perc1:            the threshold used to classify unsuccessful content creators. Creator having 
                                      total followers below the number dictated by this threshold, at the base date,
                                      are classified as unsuccessful 
                    perc2:            the threshold used to classify successful content creators. Creator having 
                                      total followers above the number dictated by this threshold, at the base date,
                                      are classified as successful
    '''

    df = oudegree_data.reset_index().iloc[:,:2]
    df.columns = ['user_id', 'followers']

    low = np.quantile(df.followers, perc1)
    high = np.quantile(df.followers, perc2)

    print("High outdegree boundary: {}".format(high))
    print("Low outdegree boundary: {}".format(low))
    
    low_outdegree_ids = df.loc[df["followers"] <= low].user_id.unique()
    high_outdegree_ids = df.loc[df["followers"] >= high].user_id.unique()
    
    
    df['outdegree_level'] = df.user_id.apply(
        lambda x: 'high' if x in high_outdegree_ids else ('low' if x in low_outdegree_ids else None))

    
    return df, low_outdegree_ids, high_outdegree_ids

In [25]:
user_outdegree_df, low_outdegree_ids, high_outdegree_ids = user_outdegree_level(user_outdegree,
                perc1 = low_user_outdegree, perc2 = high_user_outdegree)

High outdegree boundary: 162.0
Low outdegree boundary: 17.0


In the cell below, we create a list with unique ids from users that appear in the oudegree level table. This will later be uses to construct a flow-chart indicating how we lose data based on filters and operations.

In [26]:
receiver_ids = user_outdegree.index.unique()

## Non-follow Actions level

The activity level is defined as the number of actions performed by users. It is important to notice that we only observe actions targeting the 35k users that joined in march 2012. We consider this measure a proxy for the real activity level.

Let's begin by creating a dataset with all action received by those 35k users.

In [27]:
comments_received_35k = import_dta(path_dir, "12sample_comments_received.dta");
shares_received_35k = import_dta(path_dir, "12sample_reposts_received.dta");
likes_received_35k = import_dta(path_dir, "12sample_favoritings_received.dta");
messages_received_35k = import_dta(path_dir, "12sample_messages_received.dta");

if 'song_id' in shares_received_35k:
        shares_received_35k.drop(columns=["song_id"])
shares_received_35k = shares_received_35k[['reposter_id', "owner_id", 'created_at']]
shares_received_35k['outbound_activity'] = 'share'
shares_received_35k.columns = ['fan_id', 'user_id', 'date_sent', 'outbound_activity']

if 'track_id' in likes_received_35k:
        likes_received_35k = likes_received_35k.drop(columns=["track_id"])
likes_received_35k['outbound_activity'] = 'like'
likes_received_35k.columns = ['fan_id', 'user_id', 'date_sent', 'outbound_activity']

if 'track_id' in comments_received_35k:
        comments_received_35k = comments_received_35k.drop(columns=["track_id"])
comments_received_35k['outbound_activity'] = 'comment'
comments_received_35k.columns = ['fan_id', 'user_id', 'date_sent', 'outbound_activity']

messages_received_35k["outbound_activity"] = 'message'
messages_received_35k.columns = ['user_id', 'fan_id', 'date_sent', 'outbound_activity']

user_activity_data_35k = pd.concat([shares_received_35k, likes_received_35k, comments_received_35k, messages_received_35k])

%%%%%%%%%% 12sample_comments_received.dta %%%%%%%%%%
(21386, 4)
%%%%%%%%%% 12sample_reposts_received.dta %%%%%%%%%%
(83013, 4)
%%%%%%%%%% 12sample_favoritings_received.dta %%%%%%%%%%
(286903, 4)
%%%%%%%%%% 12sample_messages_received.dta %%%%%%%%%%
(17364, 3)


In [28]:
path_dir_2 = r'/Users/../Volumes/Alter_outbound_activities/'

comments_received_c = import_dta(path_dir_2, "12sample_1st_deg_comments_made.dta");
shares_received_c = import_dta(path_dir_2, "12sample_1st_deg_reposts_made.dta");
likes_received_c = import_dta(path_dir_2, "12sample_1st_deg_favoritings_made.dta");
messages_received_c = import_dta(path_dir_2, "12sample_1st_deg_messages_sent.dta");

%%%%%%%%%% 12sample_1st_deg_comments_made.dta %%%%%%%%%%
(21463011, 4)
%%%%%%%%%% 12sample_1st_deg_reposts_made.dta %%%%%%%%%%
(18953640, 4)
%%%%%%%%%% 12sample_1st_deg_favoritings_made.dta %%%%%%%%%%
(86793370, 4)
%%%%%%%%%% 12sample_1st_deg_messages_sent.dta %%%%%%%%%%
(16824074, 3)


In [29]:
if 'song_id' in shares_received_c:
        shares_received_c.drop(columns=["song_id"])
shares_received_c = shares_received_c[['reposter_id', "owner_id", 'created_at']]
shares_received_c['inbound_activity'] = 'share'
shares_received_c.columns = ['fan_id', 'user_id', 'date_sent', 'inbound_activity']

if 'track_id' in likes_received_c:
        likes_received_c = likes_received_c.drop(columns=["track_id"])
likes_received_c['inbound_activity'] = 'like'
likes_received_c.columns = ['fan_id', 'user_id', 'date_sent', 'inbound_activity']

if 'track_id' in comments_received_c:
        comments_received_c = comments_received_c.drop(columns=["track_id"])
comments_received_c['inbound_activity'] = 'comment'
comments_received_c.columns_c = ['fan_id', 'user_id', 'date_sent', 'inbound_activity']

messages_received_c["outbound_activity"] = 'message'
messages_received_c.columns = ['user_id', 'fan_id', 'date_sent', 'inbound_activity']

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/1613121866.py:15: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access
  comments_received_c.columns_c = ['fan_id', 'user_id', 'date_sent', 'inbound_activity']


In [30]:
user_activity_data_c = pd.concat([shares_received_c, likes_received_c, comments_received_c, messages_received_c])

In [31]:
def user_activity_level(user_activity_data, receiver_ids, perc1 = None, perc2 = None):
    '''Classifies users based on the amount of non-follow activities
        Arguments:
                    user_activity_data:   dataframe containing the user activities 
                    base date:             date, in datetime.datetime(YYYY, M, DD, H, M) format, in which the number 
                                           of followers per creator is calculated.
                    perc1:                 the threshold used to classify unsuccessful content creators. Creator having 
                                           total followers below the number dictated by this threshold, at the base date,
                                           are classified as unsuccessful 
                    perc2:                 the threshold used to classify successful content creators. Creator having 
                                           total followers above the number dictated by this threshold, at the base date,
                                           are classified as successful
    '''

    df = user_activity_data.groupby('fan_id', as_index = True).size()
    df = df.reindex(receiver_ids)
    print(df.shape)
    df = df.reset_index()
    df.columns = ['user_id', 'activities_performed']
    
    df.loc[df.activities_performed.isna(), 'activities_performed'] = 0
    #classification should happen after this

    low = np.quantile(df.activities_performed, perc1)
    high = np.quantile(df.activities_performed, perc2)

    print("High activity boundary: {}".format(high))
    print("Low activity boundary: {}".format(low))
    
    low_activity_ids = df.loc[df["activities_performed"] <= low].user_id.unique()
    high_activity_ids = df.loc[df["activities_performed"] > high].user_id.unique()
    
    df['activity_level'] = df.user_id.apply(
    lambda x: 'high' if x in high_activity_ids else ('low' if x in low_activity_ids else None))

    return df, low_activity_ids, high_activity_ids

In [32]:
activity_level, low_activity_ids, high_activity_ids = user_activity_level(user_activity_data_c, receiver_ids, 
                perc1 = low_user_activity, perc2 = high_user_activity)

(670746,)
High activity boundary: 70.0
Low activity boundary: 1.0


Once more we create an object containing the unique ids of users in the resulting dataset. This will be used in a flow-chart, as explained.

In [33]:
activity_ids = np.append(low_activity_ids, high_activity_ids)

# Priori response probabilities

In [35]:
table_data = user_outdegree_df.merge(activity_level, left_on = 'user_id', right_on = 'user_id', how = 'inner')
table_data.groupby(['outdegree_level', 'activity_level']).size()
table_data['Type'] = table_data.apply(lambda x: 
    'f_a' if (x.outdegree_level == 'low') & (x.activity_level == 'high')
     else ('Hermit' if (x.outdegree_level == 'low') & (x.activity_level == 'low')
     else ('Observer' if (x.outdegree_level == 'high') & (x.activity_level == 'low')
     else ('w_a' if (x.outdegree_level == 'high') & (x.activity_level == 'high')
     else 'other'))), axis=1)

hermit_ids = table_data.loc[table_data.Type =='Hermit'].user_id.unique()
w_a_ids = table_data.loc[table_data.Type =='w_a'].user_id.unique()
f_a_ids = table_data.loc[table_data.Type =='f_a'].user_id.unique()
observer_ids = table_data.loc[table_data.Type =='Observer'].user_id.unique()

In [36]:
actions_sent['user_type'] = actions_sent.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
actions_sent['creator_type'] = actions_sent.user_id.apply(
                               lambda x: 'successful' if x in successful_ids else 
                               ('unsuccessful' if x in unsuccessful_ids else 'other'))

In [37]:
actions_sent_non_fans['user_type'] = actions_sent_non_fans.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
actions_sent_non_fans['creator_type'] = actions_sent_non_fans.user_id.apply(
                                            lambda x: 'successful' if x in successful_ids else 
                                            ('unsuccessful' if x in unsuccessful_ids else 'other'))

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/4013368133.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  actions_sent_non_fans['user_type'] = actions_sent_non_fans.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else
/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/4013368133.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  actions_sent_non_fans['creator_type'] = actions_sent_non_fans.user_id.apply(


In [ ]:
import datetime
# Target Creation
delta = timedelta(days = days_delta)
mask = (actions_sent_non_fans['follower_since'] <= (actions_sent_non_fans['date_sent'] + delta))

response_df = actions_sent_non_fans.copy()
response_df.loc[mask, 'reward'] = 1
mask = response_df['reward'].isnull()
response_df.loc[mask, 'reward'] = 0

In [ ]:
attempts = response_df.groupby(['creator_type', 'user_type'], as_index = False).size()
rewards = response_df.groupby(['creator_type', 'user_type'], as_index = False).agg({'reward' : 'sum'})

priori_prob_df = rewards.merge(attempts)
priori_prob_df['P_resp_prob'] = priori_prob_df['reward']/priori_prob_df['size']
priori_prob_df 

# Indirect Return from Friends

In [49]:
# the files below contain the followers for targets that:
#1. shared creator content, 
#2. performed any action towards a creator, or
#3. followed a creator
#it was necessary do split the data because it was too large to in memory.
#on a future interaction it can be made better
import pickle as pkl
share_follower_lists = pd.read_pickle('/Users/caiorego/Desktop/BDS/RA/Seeding-Bandits/Data/alter_follower_lists.pkl')
action_follower_lists = pd.read_pickle('/Users/caiorego/Desktop/BDS/RA/Seeding-Bandits/Data/alter_follower_lists_2.pkl')
follow_follower_lists = pd.read_pickle('/Users/caiorego/Desktop/BDS/RA/Seeding-Bandits/Data/alter_follower_lists_3.pkl')

In [ ]:
#different approach, probably also good
def compute_indirect_return(df, follower_list):    
    follower_lists = follower_list
    data = df
    data = data.loc[data.user_id.isin(creators.user_id)]

    data = data.loc[data.fan_id.isin(follower_lists.index.unique())]
    data['expec_followers'] = np.nan
    data.sort_values(['user_id', 'fan_id'], inplace = True)
    
    df.date_sent = df.date_sent.dt.normalize()

    for user_id in tqdm(data.user_id.unique()):
        df_j = df.loc[df.user_id == user_id]
        for fan_id in data.loc[data.user_id == user_id].fan_id.unique():
            fan_followers = follower_lists.loc[follower_lists.index == fan_id].values[0]
            data.loc[(data.user_id == user_id)&
                                      (data.fan_id == fan_id),'expec_followers'] =\
            data.loc[(data.user_id == user_id)&
                                      (data.fan_id == fan_id)].date_sent.apply(
                lambda x : 
                np.sum(np.in1d(
                               df_j.loc[(x <= df_j.date_sent) & 
                                                      (df_j.date_sent<= x + 
                                                       timedelta(days=days_delta))
                                                     ].values,
                    fan_followers)
            ))                   
    return data

In [ ]:
def compute_stats(df):
    df['user_type'] = df.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                              ('Hermit' if x in hermit_ids else
                              ('Observer' if x in observer_ids else
                              ('w_a' if x in w_a_ids else 'other'))))

    ## classify content creators

    df['creator_type'] = df.user_id.apply(lambda x: 'successful' if x in successful_ids else 
                                                ('unsuccessful' if x in unsuccessful_ids else 'other'))
    attempts = df.groupby(['creator_type', 'user_type'], as_index = False).size()
    desc = df.groupby(['creator_type', 'user_type'], as_index = False).agg(expected_followers=('expec_followers', 'mean'),
                                   std_expected_followers=('expec_followers', 'std'),
                                   max_followers=('expec_followers', 'max'))

    return attempts.merge(desc)

In [ ]:
expec_followers_given_follow_df = compute_indirect_return(follows_received, follow_follower_lists)
indirect_return_follows = compute_stats(expec_followers_given_follow_df)

In [ ]:
indirect_return_follows 

In [ ]:
mask = user_activity_data_35k.outbound_activity == 'share'

expec_followers_given_share_df = compute_indirect_return(user_activity_data_35k.loc[mask], share_follower_lists)
indirect_return_share = compute_stats(expec_followers_given_share_df)

In [ ]:
indirect_return_share

In [ ]:
mask = user_activity_data_35k.outbound_activity == 'like'

expec_followers_given_like_df = compute_indirect_return(user_activity_data_35k.loc[mask], action_follower_lists)
indirect_return_like = compute_stats(expec_followers_given_like_df)

In [ ]:
indirect_return_like

In [ ]:
mask = user_activity_data_35k.outbound_activity == 'comment'

expec_followers_given_comment_df = compute_indirect_return(user_activity_data_35k.loc[mask], action_follower_lists)
indirect_return_comment = compute_stats(expec_followers_given_comment_df)

In [ ]:
indirect_return_comment

In [ ]:
follows_received_alters_succ = pd.read_pickle('/Users/caiorego/Desktop/BDS/RA/Seeding-Bandits/Data/follows_received_by_alters_of_successful_creators.pkl')

def get_partitions(start_date, end_date, interval = 7):
    partitions = []
    current_date = start_date

    while current_date < end_date:
        partitions.append(current_date)
        current_date += timedelta(days=interval)

    return partitions

In [346]:
#df_j previo
def compute_indirect_returns_week(df_j, week_start, fan_followers):
        array1 = df_j.loc[(week_start <= df_j.date_sent) & (df_j.date_sent <= week_start 
                    + timedelta(days=7))]
        if array1.shape[0] != 0:
            return np.sum(np.in1d(array1.fan_id.values, fan_followers))
        else:
            return 0

In [44]:
follows_received['user_type'] = follows_received.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
follows_received['creator_type'] = follows_received.user_id.apply(
                               lambda x: 'successful' if x in successful_ids else 
                               ('unsuccessful' if x in unsuccessful_ids else 'other'))

In [45]:
follows_received_filtered = follows_received.loc[(follows_received.creator_type == 'successful')
                                                 &(follows_received.user_type != 'other')]

In [46]:
#data should be 
def followers_up_to(user_id, date, data):
    data = data.loc[(data.contact_id==user_id)&(data.created_at <= date)].groupby('contact_id').fan_id.apply(np.array)
    return data

In [ ]:
# def compute_indirect_return_v2(data, follower_lists, follows_received): 
    
#     indirect_return_df = data[['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])
#     follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
    
#     follows_received = follows_received.loc[follows_received.user_id.isin(successful_ids)]
#     follows_received = follows_received.loc[follows_received.fan_id.isin(follower_lists.index.unique())]
#     data = data.loc[data.user_id.isin(creators.user_id)]
#     #data = data.loc[data.fan_id.isin(follower_lists.index.unique())]
#     for user_id in tqdm(follows_received.user_id.unique()):
#         indirect_return_list = []
#         df_j = data.loc[data.user_id == user_id]
        
#         for fan_id in follows_received.loc[follows_received.user_id == user_id].fan_id.unique():
#             fan_followers = follower_lists.loc[follower_lists.index == fan_id].values[0]
            
#             start_date = follows_received.loc[(follows_received.user_id == user_id)&
#                                               (follows_received.fan_id == fan_id)].date_sent.iloc[0]
#             end_date = datetime(2015, 5, 30)
            
#             for week_start in get_partitions(start_date, end_date):
#                 indirect_return_list.append(
#                     compute_indirect_returns_week(df_j, week_start, fan_followers)
#                 )
                
#             indirect_return_df.loc[(indirect_return_df['user_id'] == user_id)
#                                    & (indirect_return_df['fan_id'] == fan_id), 'Indirect_return'] =\
#             sum(indirect_return_list)
                                 
#     return data

In [244]:
def compute_indirect_return_v2(data, follower_lists, follows_received): 
    
    indirect_return_df = data[['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])
    follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
    end_date = datetime(2015, 5, 30)
    
    follows_received = follows_received.loc[follows_received.user_id.isin(successful_ids)]
    follows_received = follows_received.loc[follows_received.fan_id.isin(follower_lists.index.unique())]
    data = data.loc[data.user_id.isin(creators.user_id)]
    #data = data.loc[data.fan_id.isin(follower_lists.index.unique())]
    for user_id in tqdm(follows_received.user_id.unique()):
        indirect_return_list = []
        df_j = data.loc[data.user_id == user_id]
        
        for fan_id in tqdm(follows_received.loc[follows_received.user_id == user_id].fan_id.unique()):
            
            start_date = follows_received.loc[(follows_received.user_id == user_id)&
                                              (follows_received.fan_id == fan_id)].date_sent.iloc[0]
            
            for week_start in get_partitions(start_date, end_date):
                #print(fan_id)
                #print(week_start)
                try:
                    fan_followers = followers_up_to(fan_id, week_start
                            ,follows_received_alters_succ).values[0]
                except:
                    pass
                    
                indirect_return_list.append(
                    compute_indirect_returns_week(df_j, week_start, fan_followers)
                )
                
            indirect_return_df.loc[(indirect_return_df['user_id'] == user_id)
                                   & (indirect_return_df['fan_id'] == fan_id), 'Indirect_return'] =\
            sum(indirect_return_list)
                                 
    return data

In [245]:
#indirect_return_follow_df = compute_indirect_return_v2(follows_received, follow_follower_lists, follows_received_filtered)

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/1628349841.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
 22%|█████████████████████████████▏                                                                                                        | 40/184 [05:17<19:27,  8.11s/it]


  0%|▎                                                                                                                                  | 1/389 [12:30<80:54:46, 750.74s/it]


KeyboardInterrupt: 

In [ ]:
indirect_return_comment

In [ ]:
!!!!! drop fan_id == user_id

In [61]:
from joblib import Parallel, delayed

def compute_indirect_return_v2(data, follower_lists, follows_received):

    indirect_return_df = data[['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])
    follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()

    follows_received = follows_received.loc[follows_received.user_id.isin(successful_ids)]
    follows_received = follows_received.loc[follows_received.fan_id.isin(follower_lists.index.unique())]
    data = data.loc[data.user_id.isin(creators.user_id)]
    # data = data.loc[data.fan_id.isin(follower_lists.index.unique())]

    def process_user(user_id):
        indirect_return_list = []
        df_j = data.loc[data.user_id == user_id]

        for fan_id in tqdm(follows_received.loc[follows_received.user_id == user_id].fan_id.unique()):
            start_date = follows_received.loc[(follows_received.user_id == user_id) &
                                              (follows_received.fan_id == fan_id)].date_sent.iloc[0]
            end_date = datetime(2015, 5, 30)

            for week_start in get_partitions(start_date, end_date):
                try:
                    fan_followers = followers_up_to(fan_id, week_start
                            ,follows_received_alters_succ).values[0]
                except:
                    pass
                try:
                    indirect_return_list.append(
                        compute_indirect_returns_week(df_j, week_start, fan_followers)
                    )
                except:
                    pass

            
            try:
                indirect_return_df.loc[(indirect_return_df['user_id'] == user_id) &
                                   (indirect_return_df['fan_id'] == fan_id), 'Indirect_return'] = \
                sum(indirect_return_list)
            except:
                pass

    Parallel(n_jobs=7)(delayed(process_user)(user_id) for user_id in tqdm(follows_received.user_id.unique()))

    return data


In [ ]:
from joblib import Parallel, delayed

def compute_indirect_return_v1(data, follower_lists, follows_received, indirect_return_df):

    follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()

    follows_received = follows_received.loc[follows_received.user_id.isin(successful_ids)]
    follows_received = follows_received.loc[follows_received.fan_id.isin(follower_lists.index.unique())]
    data = data.loc[data.user_id.isin(creators.user_id)]
    # data = data.loc[data.fan_id.isin(follower_lists.index.unique())]

    def process_user(user_id):
        indirect_return_list = []
        df_j = data.loc[data.user_id == user_id]

        for fan_id in tqdm(follows_received.loc[follows_received.user_id == user_id].fan_id.unique()):
            start_date = follows_received.loc[(follows_received.user_id == user_id) &
                                              (follows_received.fan_id == fan_id)].date_sent.iloc[0]
            end_date = datetime(2015, 5, 30)
            fan_followers = follower_lists.loc[follower_lists.index == fan_id].values[0]
        
            for week_start in get_partitions(start_date, end_date):
                
                indirect_return_list.append(
                        compute_indirect_returns_week(df_j, week_start, fan_followers)
                    )

            indirect_return_df.loc[(indirect_return_df['user_id'] == user_id) &
                                   (indirect_return_df['fan_id'] == fan_id), 'Indirect_return'] = \
            sum(indirect_return_list)

    Parallel(n_jobs=5)(delayed(process_user)(user_id) for user_id in tqdm(follows_received.user_id.unique()))

    #return data


In [347]:
def compute_indirect_return_v3(data, follower_lists, follows_received_df, indirect_return_df): 
    
    follows_received_df['date_sent'] = follows_received_df['date_sent'].dt.normalize()
    data = data.loc[data.user_id != data.fan_id]
    
    follows_received_df = follows_received_df.loc[follows_received_df.user_id.isin(successful_ids)]
    follows_received_df = follows_received_df.loc[follows_received_df.fan_id.isin(follower_lists.index.unique())]
    data = data.loc[data.user_id.isin(creators.user_id)]
    #data = data.loc[data.fan_id.isin(follower_lists.index.unique())]
    for user_id in tqdm(follows_received_df.user_id.unique()):
        df_j = data.loc[data.user_id == user_id]
        
        for fan_id in tqdm(follows_received_df.loc[follows_received_df.user_id == user_id].fan_id.unique()):
            
            indirect_return_list = []
            
            fan_followers = follower_lists.loc[follower_lists.index == fan_id].values[0]
            
            start_date = follows_received_df.loc[(follows_received_df.user_id == user_id)&
                                              (follows_received_df.fan_id == fan_id)].date_sent.iloc[0]
            end_date = datetime(2015, 5, 30)
            
            for week_start in get_partitions(start_date, end_date):
                indirect_return_list.append(
                    compute_indirect_returns_week(df_j, week_start, fan_followers)
                )

                
            indirect_return_df.loc[(indirect_return_df['user_id'] == user_id)
                                   & (indirect_return_df['fan_id'] == fan_id), 'Indirect_return'] =\
            sum(indirect_return_list)

In [352]:
indirect_return_df = follows_received.loc[(follows_received.user_id.isin(successful_ids))&
                                          (follows_received.fan_id.isin(follow_follower_lists.index.unique()))
                                          ,['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])

compute_indirect_return_v3(follows_received, follow_follower_lists, follows_received_filtered, indirect_return_df)

indirect_return_df

indirect_return_df['user_type'] = indirect_return_df.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
indirect_return_df['creator_type'] = indirect_return_df.user_id.apply(
                               lambda x: 'successful' if x in successful_ids else 
                               ('unsuccessful' if x in unsuccessful_ids else 'other'))

indirect_return_df.dropna(inplace = True)

indirect_return_df

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/2807177332.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
 72%|█████████████████████████████████████████████████████████████████████████████████████████████████▊                                     | 42/58 [00:01<00:00, 23.78it/s]


 27%|███████████████████████████████████▉                                                                                                 | 218/806 [00:09<00:22, 26.56it/s]


 61%|█████████████████████████████████████████████████████████████████████████████████▌                                                   | 494/806 [00:20<00:12, 25.95it/s]


 62%|███████████████████████████████████████████████████████████████████████████████████▍                                                   | 21/34 [00:00<00:00, 25.07it/s]


 47%|██████████████████████████████████████████████████████████████▋                                                                      | 262/556 [00:10<00:10, 28.56it/s]


...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 39.54it/s]

 96%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊     | 374/389 [17:05<00:11,  1.26it/s]


 74%|██████████████████████████████████████████████████████████████████████████████████████████████████▋                                  | 313/422 [00:05<00:01, 61.98it/s]


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 48.21it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 40.84it/s]

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 8/8 [00:00<00:00, 122.26it/s]

 14%|███████████████████▏                                                                                                                 | 82/567 [00:00<00:02, 162.34it/s]


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 389/389 [17:25<00:00,  2.69s/it]


user_id     fan_id  Indirect_return user_type creator_type
7       37918716    7935937              4.0       w_a   successful
17      37933819    1692651              5.0       w_a   successful
28      37969361   38085515              1.0    Hermit   successful
40      38031948   15702285              2.0  Observer   successful
44      37979859     141070              3.0       w_a   successful
...          ...        ...              ...       ...          ...
432459  38224133  159432063              0.0    Hermit   successful
432481  38393304    9103936              0.0       w_a   successful
432482  38393304  112388565              0.0       w_a   successful
432483  38239638   20904612              0.0       w_a   successful
432500  38222799   90937808              0.0       w_a   successful

[40115 rows x 5 columns]

In [458]:
indirect_return_df.groupby('user_type', as_index = False).agg({'Indirect_return': 'sum'})

user_type  Indirect_return
0    Hermit           1683.0
1  Observer           3654.0
2       f_a            888.0
3       w_a         276129.0

In [353]:
mask = user_activity_data_35k.outbound_activity == 'share'
df = user_activity_data_35k.loc[mask]

indirect_return_share_df = df.loc[(df.user_id.isin(successful_ids))&
                                          (df.fan_id.isin(share_follower_lists.index.unique()))
                                          ,['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])

compute_indirect_return_v3(df, share_follower_lists, follows_received_filtered, indirect_return_share_df)

indirect_return_share_df['user_type'] = indirect_return_share_df.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
indirect_return_share_df['creator_type'] = indirect_return_share_df.user_id.apply(
                               lambda x: 'successful' if x in successful_ids else 
                               ('unsuccessful' if x in unsuccessful_ids else 'other'))

indirect_return_share_df.dropna(inplace = True)

indirect_return_share_df


/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/2807177332.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 26.19it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 38.08it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 26.99it/s]

100%|████████████████████████

 18%|███████████████████████▌                                                                                                            | 207/1157 [00:10<01:01, 15.37it/s]


 46%|█████████████████████████████████████████████████████████████                                                                       | 535/1157 [00:20<00:14, 42.95it/s]


 41%|███████████████████████████████████████████████████████▌                                                                              | 46/111 [00:01<00:02, 27.42it/s]


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 40.38it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 26.08it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 26.92it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 49.93it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 27.04it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 26.04it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 27.05it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 29.64it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 34.64it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 29.14it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.48it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 25.68it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 27.20it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 32.28it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 41.42it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 80.09it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 59.59it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 39.91it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 47.35it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 62.05it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 17/17 [00:00<00:00, 75.80it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 59.39it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 65.65it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 52.01it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 58.74it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

user_id    fan_id  Indirect_return user_type creator_type
0      38135744  33635491              0.0       w_a   successful
25     38393304  20701472             51.0       w_a   successful
32     37842894   3964813            124.0       w_a   successful
36     37842894  44866243             35.0       w_a   successful
43     38393304  46264832            151.0       w_a   successful
...         ...       ...              ...       ...          ...
82975  38398738  65298657              0.0       w_a   successful
82979  37959294  60435830              0.0       w_a   successful
82984  38112793  74377243              0.0       w_a   successful
82988  38124375  20100195              0.0       w_a   successful
82994  38445740  45705853              0.0       w_a   successful

[3054 rows x 5 columns]

In [356]:
indirect_return_share_df.groupby('user_type', as_index = False).agg({'Indirect_return': 'mean'})

user_type  Indirect_return
0    Hermit         0.272727
1  Observer         1.000000
2       f_a         2.921053
3       w_a        30.711635

In [354]:
mask = user_activity_data_35k.outbound_activity == 'like'
df = user_activity_data_35k.loc[mask]

indirect_return_like_df = df.loc[(df.user_id.isin(successful_ids))&
                                          (df.fan_id.isin(action_follower_lists.index.unique()))
                                          ,['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])

compute_indirect_return_v3(df, action_follower_lists, follows_received_filtered, indirect_return_like_df)

indirect_return_like_df['user_type'] = indirect_return_like_df.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
indirect_return_like_df['creator_type'] = indirect_return_like_df.user_id.apply(
                               lambda x: 'successful' if x in successful_ids else 
                               ('unsuccessful' if x in unsuccessful_ids else 'other'))

indirect_return_like_df.dropna(inplace = True)

indirect_return_like_df

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/2807177332.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
 33%|████████████████████████████████████████████                                                                                         | 115/347 [00:06<00:10, 21.21it/s]


  2%|██▋                                                                                                                                    | 7/344 [00:20<09:56,  1.77s/it]


 47%|███████████████████████████████████████████████████████████████▌                                                                       | 24/51 [00:00<00:01, 25.09it/s]


  4%|████▋                                                                                                                               | 100/2792 [00:05<02:36, 17.16it/s]


 11%|█████████████▉                                                                                                                      | 295/2792 [00:17<02:15, 18.47it/s]


...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 59.79it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 46.98it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 41.69it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 23/23 [00:00<00:00, 44.34it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 34.42it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 39.10it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 37.73it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 41.00it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 54.94it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 40.30it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 63.67it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 71.17it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 87/87 [00:01<00:00, 62.60it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 50.58it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 87.22it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 344/344 [04:21<00:00,  1.32it/s]


user_id     fan_id  Indirect_return user_type creator_type
31      37872188    8443087              3.0       w_a   successful
83      37928830     132959             34.0       w_a   successful
95      38027041   18498501              0.0       w_a   successful
134     38282863    8439302              0.0       w_a   successful
166     38257387    1951283              5.0       w_a   successful
...          ...        ...              ...       ...          ...
286754  38393304  127952212              0.0       w_a   successful
286831  38112793  131118411              0.0       w_a   successful
286869  38393304  148877519              0.0       f_a   successful
286873  38393304   74662633              0.0       w_a   successful
286895  38393304   19552809              0.0       w_a   successful

[7713 rows x 5 columns]

In [357]:
indirect_return_like_df.groupby('user_type', as_index = False).agg({'Indirect_return': 'mean'})

user_type  Indirect_return
0    Hermit         0.281915
1  Observer         0.000000
2       f_a         0.779310
3       w_a         9.191841

In [361]:
mask = user_activity_data_35k.outbound_activity == 'comment'
df = user_activity_data_35k.loc[mask]
df = df.loc[df.user_id != df.fan_id]

indirect_return_comment_df = df.loc[(df.user_id.isin(successful_ids))&
                                          (df.fan_id.isin(action_follower_lists.index.unique()))
                                          ,['user_id', 'fan_id']].drop_duplicates(subset=['user_id', 'fan_id'])

compute_indirect_return_v3(df, action_follower_lists, follows_received_filtered, indirect_return_comment_df)

indirect_return_comment_df['user_type'] = indirect_return_comment_df.fan_id.apply(lambda x: 'f_a' if x in f_a_ids else 
                          ('Hermit' if x in hermit_ids else
                          ('Observer' if x in observer_ids else
                          ('w_a' if x in w_a_ids else 'other'))))

## classify content creators
indirect_return_comment_df['creator_type'] = indirect_return_comment_df.user_id.apply(
                               lambda x: 'successful' if x in successful_ids else 
                               ('unsuccessful' if x in unsuccessful_ids else 'other'))

indirect_return_comment_df.dropna(inplace = True)

indirect_return_comment_df

/var/folders/f2/cgjzt69n5hlgmtsm36p1pztw0000gn/T/ipykernel_51968/2807177332.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  follows_received['date_sent'] = follows_received['date_sent'].dt.normalize()
 48%|████████████████████████████████████████████████████████████████                                                                     | 167/347 [00:06<00:06, 29.81it/s]


 23%|██████████████████████████████▎                                                                                                       | 48/212 [00:01<00:06, 24.49it/s]


  0%|                                                                                                                                                 | 0/9 [00:00<?, ?it/s]


  9%|███████████▍                                                                                                                        | 242/2792 [00:11<01:54, 22.32it/s]


 19%|████████████████████████▍                                                                                                           | 518/2792 [00:24<01:31, 24.80it/s]


...

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 34.44it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 33.15it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 96.74it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 92.83it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 44.36it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 53.46it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:00<00:00, 43.75it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 23/23 [00:00<00:00, 51.10it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 36.51it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 49.95it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 39.02it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 41.93it/s]

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10/10 [00:00<00:00, 114.86it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 47.89it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 11/11 [00:00<00:00, 46.61it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 54.79it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 54.14it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 57.59it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10/10 [00:00<00:00, 88.95it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 57.89it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████

user_id    fan_id  Indirect_return user_type creator_type
15     38381896  14913429              0.0       w_a   successful
22     38282863    796798              1.0       w_a   successful
23     38393304  38184762            417.0       w_a   successful
42     38393304  24802926             51.0       w_a   successful
50     38393304  43113985             25.0       w_a   successful
...         ...       ...              ...       ...          ...
21363  38404408  33023682              0.0       w_a   successful
21364  38186609    485346             27.0       w_a   successful
21366  38218659   4363521              0.0       w_a   successful
21374  38393304  50947411             25.0       w_a   successful
21381  37868261  14144117              1.0       w_a   successful

[1649 rows x 5 columns]

In [457]:
indirect_return_comment_df.groupby('user_type', as_index = False).agg({'Indirect_return': 'mean'})

user_type  Indirect_return
0    Hermit             40.0
1  Observer              0.0
2       f_a            184.0
3       w_a          36612.0

In [ ]:


compute_indirect_return_v3(follows_received, follow_follower_lists, follows_received_filtered, indirect_return_df)


In [366]:
data = follows_received
follows_received_df = follows_received
follower_lists = follow_follower_lists

follows_received_df['date_sent'] = follows_received_df['date_sent'].dt.normalize()
    
follows_received_df = follows_received_df.loc[follows_received_df.user_id.isin(successful_ids)]
follows_received_df = follows_received_df.loc[follows_received_df.fan_id.isin(follower_lists.index.unique())]
data = data.loc[data.user_id.isin(creators.user_id)]
    

In [380]:
follows_received_df

fan_id   user_id  date_sent user_type creator_type
7         7935937  37918716 2013-03-02       w_a   successful
17        1692651  37933819 2013-03-02       w_a   successful
18       29655624  38022175 2013-03-03     other   successful
20        1540436  38027041 2013-03-03     other   successful
28       38085515  37969361 2013-03-03    Hermit   successful
...           ...       ...        ...       ...          ...
432481    9103936  38393304 2015-06-28       w_a   successful
432482  112388565  38393304 2015-06-28       w_a   successful
432483   20904612  38239638 2015-06-28       w_a   successful
432500   90937808  38222799 2015-06-30       w_a   successful
432501    4203669  37881808 2015-06-30     other   successful

[106616 rows x 5 columns]

In [442]:
user_id = 38393304

df_j = data.loc[data.user_id == user_id]

for fan_id in follows_received_df.loc[follows_received_df.user_id == user_id].fan_id.unique():

    indirect_return_list = []

    fan_followers = follower_lists.loc[follower_lists.index == fan_id].values[0]

    start_date = follows_received_df.loc[(follows_received_df.user_id == user_id)&
                                      (follows_received_df.fan_id == fan_id)].date_sent.iloc[0]
    end_date = datetime(2015, 5, 30)

    for week_start in get_partitions(start_date, end_date):
        indirect_return_list.append(
            compute_indirect_returns_week(df_j, week_start, fan_followers)
        )


    indirect_return_df.loc[(indirect_return_df['user_id'] == user_id)
                           & (indirect_return_df['fan_id'] == fan_id), 'Indirect_return'] =\
    sum(indirect_return_list)


KeyboardInterrupt: 

In [452]:
indirect_return_list = []
user_id = 38027041

fan_id = 1540436
df_j = data.loc[data.user_id == user_id]
fan_followers = follower_lists.loc[follower_lists.index == fan_id].values[0]

start_date = follows_received_df.loc[(follows_received_df.user_id == user_id)&
                                      (follows_received_df.fan_id == fan_id)].date_sent.iloc[0]
end_date = datetime(2015, 6, 30)

for week_start in get_partitions(start_date, end_date):
    
    print(week_start)
    print(compute_indirect_returns_week(df_j, week_start, fan_followers))


2013-03-03 00:00:00
0
2013-03-10 00:00:00
0
2013-03-17 00:00:00
0
2013-03-24 00:00:00
0
2013-03-31 00:00:00
0
2013-04-07 00:00:00
0
2013-04-14 00:00:00
0
2013-04-21 00:00:00
0
2013-04-28 00:00:00
0
2013-05-05 00:00:00
0
2013-05-12 00:00:00
0
2013-05-19 00:00:00
0
2013-05-26 00:00:00
0
2013-06-02 00:00:00
0
2013-06-09 00:00:00
0
2013-06-16 00:00:00
0
2013-06-23 00:00:00
0
2013-06-30 00:00:00
0
2013-07-07 00:00:00
0
2013-07-14 00:00:00
0
2013-07-21 00:00:00
0
2013-07-28 00:00:00
0
2013-08-04 00:00:00
0
2013-08-11 00:00:00
0
2013-08-18 00:00:00
0
2013-08-25 00:00:00
0
2013-09-01 00:00:00
0
2013-09-08 00:00:00
0
2013-09-15 00:00:00
0
2013-09-22 00:00:00
0
2013-09-29 00:00:00
0
2013-10-06 00:00:00
0
2013-10-13 00:00:00
0
2013-10-20 00:00:00
0
2013-10-27 00:00:00
0
2013-11-03 00:00:00
0
2013-11-10 00:00:00
0
2013-11-17 00:00:00
0
2013-11-24 00:00:00
0
2013-12-01 00:00:00
0
2013-12-08 00:00:00
0
2013-12-15 00:00:00
0
2013-12-22 00:00:00
0
2013-12-29 00:00:00
0
2014-01-05 00:00:00
0
2014-01-12

In [453]:
follows_received_df.loc[(follows_received_df.user_id == user_id)&
                                      (follows_received_df.fan_id == fan_id)].date_sent.iloc[0]

Timestamp('2013-03-03 00:00:00')

In [454]:
df_j.loc[(datetime(2013, 5, 30) <= df_j.date_sent) & (datetime(2013, 5, 30) <= week_start 
                    + timedelta(days=7))].fan_id.values

array([40688349,  6145359, 30255203, ..., 11763947, 20574006, 76685725],
      dtype=int32)

In [455]:
date = datetime(2013, 4, 27)

a = df_j.loc[(date <= df_j.date_sent) & (date <= week_start 
                    + timedelta(days=7))].fan_id.values
a[np.in1d(a,fan_followers)]

array([], dtype=int32)

In [456]:
date = datetime(2013, 3, 2)

a = df_j.loc[(date <= df_j.date_sent) & (date <= week_start 
                    + timedelta(days=7))].fan_id.values
a[np.in1d(a,fan_followers)]

array([], dtype=int32)

In [438]:
date = datetime(2013, 3, 9)

a = df_j.loc[(date <= df_j.date_sent) & (date <= week_start 
                    + timedelta(days=7))].fan_id.values
a[np.in1d(a,fan_followers)]

array([2023723], dtype=int32)

In [440]:
date = datetime(2015, 3, 20)

a = df_j.loc[(date <= df_j.date_sent) & (date <= week_start 
                    + timedelta(days=7))].fan_id.values
a[np.in1d(a,fan_followers)]

array([], dtype=int32)

In [441]:
follows_received.loc[(follows_received.user_id == 37918716)&(follows_received.fan_id == 2023723)]

fan_id   user_id  date_sent user_type creator_type
49656  2023723  37918716 2013-04-30     other   successful